In [1]:
%time df = pd.read_csv('/xfs/sample.csv')
df.info()

CPU times: user 1min 8s, sys: 7.72 s, total: 1min 16s
Wall time: 1min 16s
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 92331988 entries, 0 to 92331987
Data columns (total 7 columns):
time           int64
amount         float64
exch           object
price          float64
server_time    int64
side           object
ticker         object
dtypes: float64(2), int64(2), object(3)
memory usage: 4.8+ GB


In [2]:
df.head()

time  amount  exch      price          server_time side  \
0  1561939200002479372  1.4894  bnce   292.7000  1561939199919000064  NaN   
1  1561939200011035644  0.0833  btfx 10809.0000  1561939199927000064  bid   
2  1561939200011055712  0.8333  btfx 10809.0000  1561939199927000064  bid   
3  1561939200019037617  0.0831  bnce 10854.1000  1561939199935000064  NaN   
4  1561939200026450471  0.1250  okex   123.2100  1561939200026450432  ask   

    ticker  
0  eth_usd  
1  btc_usd  
2  btc_usd  
3  btc_usd  
4  ltc_usd

In [7]:
SECOND = int(1e9)

example_time = 1567295920000000000

last_5min = (df['time'] > example_time - SECOND * 60 * 5) & (df['time'] <= example_time)
last_15min = (df['time'] > example_time - SECOND * 60 * 15) & (df['time'] <= example_time)
last_60min = (df['time'] > example_time - SECOND * 60 * 60) & (df['time'] <= example_time)
of_btc_usd = df['ticker'] == 'btc_usd'
of_gdax = df['exch'] == 'gdax'
of_bmex = df['exch'] == 'bmex'

g5 = last_5min & of_btc_usd & of_gdax
b5 = last_5min & of_btc_usd & of_bmex
g15 = last_15min & of_btc_usd & of_gdax
b15 = last_15min & of_btc_usd & of_bmex
g60 = last_60min & of_btc_usd & of_gdax
b60 = last_60min & of_btc_usd & of_bmex

ratio_5min = ((df.loc[b5, 'price'] * df.loc[b5, 'amount']).sum() / df.loc[b5, 'amount'].sum()) / ((df.loc[g5, 'price'] * df.loc[g5, 'amount']).sum() / df.loc[g5, 'amount'].sum())
ratio_15min = ((df.loc[b15, 'price'] * df.loc[b15, 'amount']).sum() / df.loc[b15, 'amount'].sum()) / ((df.loc[g15, 'price'] * df.loc[g15, 'amount']).sum() / df.loc[g15, 'amount'].sum())
ratio_60min = ((df.loc[b60, 'price'] * df.loc[b60, 'amount']).sum() / df.loc[b60, 'amount'].sum()) / ((df.loc[g60, 'price'] * df.loc[g60, 'amount']).sum() / df.loc[g60, 'amount'].sum())

abs(ratio_5min - 1.000474060563638) < 1e-6, abs(ratio_15min - 1.0005019306061411) < 1e-6, abs(ratio_60min - 1.0002338013889658) < 1e-6

(True, True, True)

In [8]:
ref = pd.read_csv('../var/hard.csv')
ref.head()

time       last  bmex_5min  gdax_5min  n_bmex_p5  n_gdax_p5  \
0  1561939210000000000 10758.5800 10760.7205 10760.4593         22         28   
1  1561939220000000000 10770.0000 10763.6811 10761.2528        230         75   
2  1561939230000000000 10758.0100 10761.8843 10760.1596        418        120   
3  1561939240000000000 10752.5000 10757.6829 10760.3630        507        147   
4  1561939250000000000 10772.6900 10757.5702 10763.0840        537        191   

      r5    r15    r60  
0 1.0000 1.0000 1.0000  
1 1.0002 1.0002 1.0002  
2 1.0002 1.0002 1.0002  
3 0.9998 0.9998 0.9998  
4 0.9995 0.9995 0.9995

In [12]:
ref['time'].tail(25).values

array([1567295750000000000, 1567295760000000000, 1567295770000000000, 1567295780000000000, 1567295790000000000, 1567295800000000000, 1567295810000000000, 1567295820000000000, 1567295830000000000,
       1567295840000000000, 1567295850000000000, 1567295860000000000, 1567295870000000000, 1567295880000000000, 1567295890000000000, 1567295900000000000, 1567295910000000000, 1567295920000000000,
       1567295930000000000, 1567295940000000000, 1567295950000000000, 1567295960000000000, 1567295970000000000, 1567295980000000000, 1567295990000000000])

In [13]:
import time

start = time.time()
rows = []

for example_time in ref['time'].tail(25).values:
    last_5min = (df['time'] > example_time - SECOND * 60 * 5) & (df['time'] <= example_time)
    last_15min = (df['time'] > example_time - SECOND * 60 * 15) & (df['time'] <= example_time)
    last_60min = (df['time'] > example_time - SECOND * 60 * 60) & (df['time'] <= example_time)
    of_btc_usd = df['ticker'] == 'btc_usd'
    of_gdax = df['exch'] == 'gdax'
    of_bmex = df['exch'] == 'bmex'

    g5 = last_5min & of_btc_usd & of_gdax
    b5 = last_5min & of_btc_usd & of_bmex
    g15 = last_15min & of_btc_usd & of_gdax
    b15 = last_15min & of_btc_usd & of_bmex
    g60 = last_60min & of_btc_usd & of_gdax
    b60 = last_60min & of_btc_usd & of_bmex

    ratio_5min = ((df.loc[b5, 'price'] * df.loc[b5, 'amount']).sum() / df.loc[b5, 'amount'].sum()) / ((df.loc[g5, 'price'] * df.loc[g5, 'amount']).sum() / df.loc[g5, 'amount'].sum())
    ratio_15min = ((df.loc[b15, 'price'] * df.loc[b15, 'amount']).sum() / df.loc[b15, 'amount'].sum()) / ((df.loc[g15, 'price'] * df.loc[g15, 'amount']).sum() / df.loc[g15, 'amount'].sum())
    ratio_60min = ((df.loc[b60, 'price'] * df.loc[b60, 'amount']).sum() / df.loc[b60, 'amount'].sum()) / ((df.loc[g60, 'price'] * df.loc[g60, 'amount']).sum() / df.loc[g60, 'amount'].sum())
    rows.append(dict(example_time=example_time, r5=ratio_5min, r15=ratio_15min, r60=ratio_60min))
    
took = time.time() - start
print('finished in {:.1f}sec'.format(took))

finished in 487.8sec


In [19]:
hypothetical_full_took = (took / 25) * 5401808
hypothetical_full_took / 60 / 60 / 24 / 365

3.342554545733013

In [20]:
92331988 / 908204336

0.1016643329480867

In [21]:
took / 25

19.513984975814818

In [24]:
'{:,.1f}'.format(hypothetical_full_took), hypothetical_full_took

('105,410,800.2', 105410800.15423629)

In [32]:
(pd.DataFrame(rows).join(ref.set_index('time'), on='example_time', rsuffix='_rust')
 .assign(r5_delta=lambda df: abs(df['r5'] - df['r5_rust']))
 .assign(r15_delta=lambda df: abs(df['r15'] - df['r15_rust']))
 .assign(r60_delta=lambda df: abs(df['r60'] - df['r60_rust']))
)[['r5_delta','r15_delta','r60_delta']].max(axis=0).map(lambda x: '{:.15f}'.format(x))

r5_delta     0.000000000002368
r15_delta    0.000000000010704
r60_delta    0.000000000005513
dtype: object